## ELEX 4653 Quiz 1

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

### Question 1

Write a function `carea(r,l)` that returns the area of a cylinder calculated using the formula:
$$ V = \pi r^2 l $$
For example, `carea(2,3)` should return approximately 37.7. You can use 3.14 for the value of $\pi$.

### Question 2

Write a function `sumsquares(l)` that returns the sum of the squares of the numbers in the list `l`.

For example, `sumsquares([1,2,3])` should return `14`.

### Question 3

Write a function `concat(a,b)` where `a` and `b` are lists of strings that returns a list containing the concatenation (joining) of pairs of strings taken from `a` and `b`.

For example `concat(['a','bc','def'],['ghi','jk','lmn'])` would return `['aghi', 'bcjk', 'deflmn']`.

In [25]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
    
    n = 0     # question number
    trial = 0 # test number
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.search(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.search(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l

    # list of n random integers
    def randints(n,*args,**kwargs):
        return [randint(*args,**kwargs) for _ in range(n)]

    # list of uniformly distribute random numbers
    def randoms(n,*args,**kwargs):
        return [random.uniform(*args,**kwargs) for _ in range(n)]
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    import math
    def roundn(num, n):
        return 0 if not num else round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))

    def ch(s,n=(1,1)):
        return randwords(1,chars=s,nl=n)[0]

    def Q(f,*a,rounding=False):
        oa = copy.deepcopy(a)
        r = f(*a)
        r = roundn(r,2) if rounding else r
        return (r,f"{f.__name__}{repr(oa)} returns {repr(r)}")

    def Q1():
        return Q(carea,randint(1,10),randint(1,10),rounding=True)

    def Q2():
        return Q(sumsquares, [randint(-3,5) for _ in range(randint(3,5))] )
       
    def Q3():
        nw = randint(3,5)
        return Q(concat,randwords(nw),randwords(nw))

    hashvalues = '''
W4yFPxlYkTppkTppHcANK0BLil5+kTppkxSJHLyW
2302gBsnkx2S3qOrlUHRPpKvSIma+Hd62302Fypz
mG3wxOkhFh58QJ/oPZpBWaHy2P+00J4UTZmNjmkR
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        trial = 0
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                traceback.print_exc()
                err = f"Error during test {n}: {e}"
            trial += 1
        if testing:
           newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)


labcheck(0)
#labcheck(1)